In [2]:
import pandas as pd
import numpy as np
import plotly.express as px
from pyproj import Proj

from sklearn.ensemble import RandomForestClassifier, RandomForestRegressor
from sklearn.neighbors import KNeighborsRegressor, KNeighborsClassifier
from sklearn.multioutput import MultiOutputClassifier, MultiOutputRegressor
from sklearn.model_selection import train_test_split
from post_processing import plot_results, evaluate_model, l2_dist
import sqlalchemy
import warnings
warnings.filterwarnings('ignore')

# Postgres query

In [3]:
DB_URL = 'postgresql+psycopg2://hospitrackadmin@hospitrack:HospiTrack34@hospitrack.postgres.database.azure.com/hospitrack'
engine = sqlalchemy.create_engine(DB_URL)
df = pd.read_sql('select * from public.demo_router_scans', con=engine)
print(df.shape)
df.head(2)

(2459, 8)


row_id          id      timestamp  longitude   latitude  altitude  \
0    6340  67464705.0  1582179360515  34.769125  32.073358      42.0   
1    6341  31780742.0  1582179370668  34.769050  32.073462      42.0   

   accuracy                                      rssi_by_bssid  
0    15.462  {'00:0e:f4:dd:f9:de': -77.0, '00:b8:c2:12:d3:3...  
1    13.115  {'00:0e:f4:dd:f9:de': -63.0, '00:b8:c2:32:87:1...

In [18]:
df['rssi_by_bssid'] = df.apply(lambda x : pd.concat([pd.DataFrame([x['timestamp']]).rename(columns={0:1}), 
                                                     pd.DataFrame((x['rssi_by_bssid']).items()).set_index(0)],
                                                    axis=0).T.set_index(0) ,axis=1)
X = pd.concat(df['rssi_by_bssid'].tolist())

myProj = Proj("+proj=utm +zone=36k, +north +ellps=WGS84 +datum=WGS84 +units=m +no_defs")
Y = pd.DataFrame(df.apply(lambda x: myProj(x.longitude, x.latitude),
                                      axis=1).tolist(), index=df.index).rename(columns={0:'x', 1:'y'})
print(X.shape)
X.head()

(2459, 2640)


00:0e:f4:dd:f9:de  00:b8:c2:12:d3:35  00:b8:c2:47:06:22  \
0                                                                       
1.582179e+12              -77.0              -88.0              -79.0   
1.582179e+12              -63.0                NaN              -73.0   
1.582179e+12              -63.0              -89.0              -74.0   
1.582179e+12              -75.0                NaN              -75.0   
1.582179e+12              -85.0                NaN              -68.0   

              08:3e:5d:5a:a1:74  10:be:f5:35:7b:38  14:ae:db:47:47:dd  \
0                                                                       
1.582179e+12              -71.0              -86.0              -85.0   
1.582179e+12              -78.0                NaN              -77.0   
1.582179e+12              -78.0                NaN              -84.0   
1.582179e+12              -77.0              -91.0              -89.0   
1.582179e+12              -80.0                NaN                NaN   

              14:ae:db:50:55:6d  14:ae:db:b1:aa:6d  14:ae:db:ce:a0:9d  \
0                                                                       
1.582179e+12              -85.0              -88.0              -72.0   
1.582179e+12              -87.0              -78.0              -79.0   
1.582179e+12              -86.0              -79.0                NaN   
1.582179e+12                NaN              -80.0                NaN   
1.582179e+12                NaN              -77.0                NaN   

              14:ae:db:ce:c8:fd  ...  74:4d:28:00:3f:5a  80:2a:a8:b5:ab:c1  \
0                                ...                                         
1.582179e+12              -64.0  ...                NaN                NaN   
1.582179e+12              -75.0  ...                NaN                NaN   
1.582179e+12              -75.0  ...                NaN                NaN   
1.582179e+12              -75.0  ...                NaN                NaN   
1.582179e+12              -79.0  ...                NaN                NaN   

              00:b8:c2:29:79:48  08:97:58:32:60:f2  32:cd:a7:fa:f1:dd  \
0                                                                       
1.582179e+12                NaN                NaN                NaN   
1.582179e+12                NaN                NaN                NaN   
1.582179e+12                NaN                NaN                NaN   
1.582179e+12                NaN                NaN                NaN   
1.582179e+12                NaN                NaN                NaN   

              34:0a:91:15:21:66  80:2a:a8:b5:aa:d1  94:8f:cf:ad:8f:3b  \
0                                                                       
1.582179e+12                NaN                NaN                NaN   
1.582179e+12                NaN                NaN                NaN   
1.582179e+12                NaN                NaN                NaN   
1.582179e+12                NaN                NaN                NaN   
1.582179e+12                NaN                NaN                NaN   

              f8:e9:03:13:55:44  90:a7:c1:13:1e:b4  
0                                                   
1.582179e+12                NaN                NaN  
1.582179e+12                NaN                NaN  
1.582179e+12                NaN                NaN  
1.582179e+12                NaN                NaN  
1.582179e+12                NaN                NaN  

[5 rows x 2640 columns]

In [17]:
print(Y.shape)
Y.head()

(2459, 2)


x             y
0  666981.788700  3.549936e+06
1  666974.482216  3.549948e+06
2  666974.482216  3.549948e+06
3  666983.811626  3.549961e+06
4  666987.404883  3.549965e+06

## Location prediction

In [19]:
X_train, X_test, y_train, y_test = train_test_split(X.fillna(-200), Y, 
                                                  random_state=42, 
                                                  test_size=0.3, shuffle=True)

In [20]:
model = MultiOutputRegressor(RandomForestRegressor(random_state=1))
multi_target_forest = model.fit(X_train, y_train)
y_pred = multi_target_forest.predict(X_test)
y_test['pred_x'] = y_pred[:, 0]
y_test['pred_y'] = y_pred[:, 1]

In [22]:
l2dists_mean, l2dists = l2_dist((y_test['pred_x'], y_test['pred_y']), (y_test['x'], y_test['y']))
y_test['dist'] = list(l2dists)

srt = np.sort(l2dists)
n = len(srt)
prec_90 = srt[int(0.9*n)]
print("mean distances : " + str(l2dists.mean()))
print("median : " + str(srt[int(0.5*n)]))
print("90 percentile : " + str(prec_90))

mean distances : 15.489476084862766
median : 10.187214333636547
90 percentile : 31.60504905649355


In [33]:
y_test[['longitude', 'latitude']] = pd.DataFrame(y_test.apply(lambda x: myProj(x.x, x.y, inverse=True)
                                                , axis=1).tolist(), index=y_test.index)
fig = px.scatter_mapbox(y_test, lat="latitude", lon="longitude",
                         color='dist', zoom=16, height=500,)
fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

# Reading UJI data

In [2]:
Trainingdf = pd.read_csv('TrainingData.csv')
Validationdf = pd.read_csv('ValidationData.csv')
df = pd.concat([Trainingdf, Validationdf], ignore_index=True)
df.head(2)

WAP001  WAP002  WAP003  WAP004  WAP005  WAP006  WAP007  WAP008  WAP009  \
0     100     100     100     100     100     100     100     100     100   
1     100     100     100     100     100     100     100     100     100   

   WAP010  ...  WAP520  LONGITUDE      LATITUDE  FLOOR  BUILDINGID  SPACEID  \
0     100  ...     100 -7541.2643  4.864921e+06      2           1      106   
1     100  ...     100 -7536.6212  4.864934e+06      2           1      106   

   RELATIVEPOSITION  USERID  PHONEID   TIMESTAMP  
0                 2       2       23  1371713733  
1                 2       2       23  1371713691  

[2 rows x 529 columns]

## Location prediction

In [3]:
X = df[df.columns[0:len(df.columns)-9]]
Y = df[['LONGITUDE','LATITUDE']]
X_train, X_test, y_train, y_test = train_test_split(X, Y, 
                                                  random_state=42, 
                                                  test_size=0.3, shuffle=True)

In [4]:
model = MultiOutputRegressor(RandomForestRegressor(random_state=1))
multi_target_forest = model.fit(X_train, y_train)
y_pred = multi_target_forest.predict(X_test)
y_test['pred_x'] = y_pred[:, 0]
y_test['pred_y'] = y_pred[:, 1]

In [5]:
l2dists_mean, l2dists = l2_dist((y_test['pred_x'], y_test['pred_y']), (y_test['LONGITUDE'], y_test['LATITUDE']))
y_test['dist'] = list(l2dists)

srt = np.sort(l2dists)
n = len(srt)
prec_90 = srt[int(0.9*n)]
print("mean distances : " + str(l2dists.mean()))
print("median : " + str(srt[int(0.5*n)]))
print("90 percentile : " + str(prec_90))

mean distances : 6.055419620106044
median : 3.5352180528246513
90 percentile : 13.507243651269079


In [ ]:
fig = px.scatter_mapbox(y_test, lat="LATITUDE", lon="LONGITUDE", hover_name="USERID", hover_data=["BUILDINGID", "FLOOR", "SPACEID"],
                        color="USERID", zoom=16, height=500,)
fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

## Buliding prediction

In [6]:
X = df[df.columns[0:len(df.columns)-9]]
Y = df['BUILDINGID']
X_train, X_test, y_train, y_test = train_test_split(X, Y, 
                                                  random_state=42, 
                                                  test_size=0.3, shuffle=True)

In [7]:
model = RandomForestClassifier(random_state=1)
y_pred = model.fit(X_train, y_train).predict(X_test)
evaluate_model(y_test, y_pred)

Confusion matrix:
[[1742    0    0]
 [   1 1625   13]
 [   0    0 2934]]
f1 Score :  0.9977377772836262
Accuracy Score : 0.9977830562153602
Precision Score :  0.9983383369469281
Recall Score :  0.997152735407769
MCC Score : 0.9965447948547613


## Floor prediction

In [8]:
df2 = df[df['BUILDINGID']==2]
X = df2[df2.columns[0:len(df2.columns)-9]]
Y = df2['FLOOR']
X_train, X_test, y_train, y_test = train_test_split(X, Y, 
                                                  random_state=42, 
                                                  test_size=0.3, shuffle=True)

In [9]:
model = RandomForestClassifier(random_state=1)
y_pred = model.fit(X_train, y_train).predict(X_test)
evaluate_model(y_test, y_pred)

Confusion matrix:
[[595   0   0   0   0]
 [ 13 637   5   1   0]
 [  6  19 472   5   0]
 [  0   2   7 829   0]
 [  0   0   1   7 329]]
f1 Score :  0.9770339039089333
Accuracy Score : 0.9774590163934426
Precision Score :  0.9789793854671462
Recall Score :  0.975359379997017
MCC Score : 0.9712802283034752


## Visualization with interactive map

In [10]:
myProj = Proj(init='epsg:3857')
df[['longitude_geo', 'latitude_geo']] = pd.DataFrame(df.apply(lambda x: myProj(x.LONGITUDE, x.LATITUDE, inverse=True), axis=1).tolist(), index=df.index)

In [16]:
fig = px.scatter_mapbox(df, lat="latitude_geo", lon="longitude_geo", hover_name="USERID", hover_data=["BUILDINGID", "FLOOR", "SPACEID"],
                        color="USERID", zoom=16, height=500, animation_frame='FLOOR')
fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [41]:
folium.Map(zoom_start=6, tiles='https://{s}.basemaps.cartocdn.com/rastertiles/voyager/{z}/{x}/{y}{r}.png', 
           attr='&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors &copy; <a href="https://carto.com/attributions">CARTO</a>')
m.save('test123.html')
m